In [1]:
import django
import os
import pandas as pd
import numpy as np
import html
import namedentities as ne
from old_database.modules_webpage import entry_to_dict #read_publications, read_addresses, read_seminars
import time

os.environ.setdefault("DJANGO_SETTINGS_MODULE", "nanotud.settings")
from django.core.wsgi import get_wsgi_application
application = get_wsgi_application()
#from research.models import Publication


#from home.models import Room, Country, Title_full, Gender, Status
from internal.models import Member
from external.models import Presentation
from home.models import Event_type, Presentation_type
#from teaching.models import Seminar

# needed when run inter jupyter enviornment:
os.environ["DJANGO_ALLOW_ASYNC_UNSAFE"] = "true"
django.setup()

#import gender_guesser.detector as gender
import re


FileNotFoundError: [Errno 2] No such file or directory: '/etc/config.json'

## Write old papers database

In [2]:
def read_addresses(file_name):
    
    with open(file_name, 'r',encoding='utf-8',errors='replace') as file:
            content = file.read() 
    all_entries = content.split('enditem')
    
    for entry in all_entries:
        dictio = entry_to_dict(entry)
        if dictio != {}:
            try:
                df = df.append(dictio, ignore_index=True)     # append new entry to DF
            except:
                df = pd.DataFrame(dictio, index=[0])          # first time create the DF
    df = df.fillna(np.NaN)
    #ind = df[df['vorname'].isna() & df['nachname'].isna()].index.values
    #df.drop(ind,inplace=True)
    return df

In [3]:
path_presentation = 'old_database/database_mod.conferences'
df_presentation = read_addresses(path_presentation)


In [4]:
df_presentation.columns

Index(['type', 'sliderefpdf', 'nonmiei', 'abstractrefpdf', 'conference',
       'conferenceref', 'year', 'month', 'days', 'where', 'field', 'title',
       'authors', 'abstract', 'authorsref', 'day', 'department', 'host',
       'hostref', 'hour', 'invitedby', 'invitedfor', '', 'whereref',
       'authorref', '[1]', '[2]', 'abstractref', 'abstractrefpsgz',
       'conferencerefpdf', 'slideref', 'conflogo', 'conferencejpg',
       'sliderefpsgz'],
      dtype='object')

**Write to Django Database**

In [5]:
for index, row in df_presentation.iterrows():
    comment_date_raw_l=[]
    no_speaker=False
    if type(row['year'])!= float: # or row['year']!='':
        year_raw=row['year']
        year_list=year_raw.split('-')
        year_start_raw=year_list[0]
        year_end_raw=year_list[-1]
    else:
        year_raw=None
    if type(row['month'])!=float: # or row['month']!='':
        month_raw=row['month']
        month_list=month_raw.split('-')
        month_start_raw=month_list[0]
        month_end_raw=month_list[-1]
        if month_start_raw=='':
            month_start_raw='01'
            month_end_raw='01'
            comment_date_raw_l.append('Unknown month')
    else:
        month_start_raw='01'
        month_end_raw='01'
        comment_date_raw_l.append('Unknown month')
    if type(row['day'])!=float and type(row['days'])==float: # or row['days']!='':
        day_raw=row['day']
        day_list=day_raw.split('-')
        day_start_raw=day_list[0]
        day_end_raw=day_list[-1]
        for c_str in day_end_raw:
            if '(' == c_str:
                print('jolo')
                temp_l=day_end_raw.split('(')
                print('temp_l',temp_l)
                day_end_raw=temp_l[0]
                month_end_raw=temp_l[1].strip(')')
        if day_start_raw=='':
            day_start_raw='01'
            day_end_raw='01'
            comment_date_raw_l.append('Unknown day')
    elif type(row['days'])!=float and type(row['day'])==float: # or row['days']!='':
        day_raw=row['days']
        day_list=day_raw.split('-')
        day_start_raw=day_list[0]
        day_end_raw=day_list[-1]
        for c_str in day_end_raw:
            if '(' == c_str:
                print('jolo')
                temp_l=day_end_raw.split('(')
                print('temp_l',temp_l)
                day_end_raw=temp_l[0]
                month_end_raw=temp_l[1].strip(')')
        if day_start_raw=='':
            day_start_raw='01'
            day_end_raw='01'
            comment_date_raw_l.append('Unknown day')
    else:
        day_start_raw='01'
        day_end_raw='01'
        comment_date_raw_l.append('Unknown day')
    if type(row['hour'])!=float: # or row['days']!='':
        try:
            int(row['hour'][0].strip())
            hour_raw=row['hour']
            hour_list=hour_raw.split('-')
            time_start_raw=hour_list[0].strip()
            time_end_raw=hour_list[-1].strip()
        except:
            time_start_raw=None
            time_end_raw=None
    else:
        time_start_raw=None
        time_end_raw=None
    public_raw=True
    if row['title']!=float:
        title_raw = html.unescape(row['title'])
    else:
        title_raw=None
    if type(row['nonmiei'])!=float:
        if row['nonmiei']=='no' or row['nonmiei']=='No' or row['nonmiei']=='NO':
            nonmiei_raw=False
        else:
            nonmiei_raw=True
    else:
        nonmiei_raw=False
    if type(row['conferencejpg'])!=float:
        #copyright_raw=row['url']
        image_raw=row['conferencejpg']
    else:
        image_raw=None
    if type(row['hostref'])!=float:
        #copyright_raw=row['url']
        host_url_raw=row['hostref']
    elif type(row['whereref'])!=float:
        #copyright_raw=row['url']
        host_url_raw=row['whereref']
    else:
        host_url_raw=None
    if type(row['invitedby'])!=float:
        host_person_raw=html.unescape(row['invitedby'])
    else:
        host_person_raw=None
    if type(row['slideref'])!=float:
        slide_ref_raw=html.unescape(row['slideref'])
    else:
        slide_ref_raw=None
    if type(row['abstractref'])!=float:
        abstract_ref_raw=html.unescape(row['abstractref'])
    else:
        abstract_ref_raw=None
    if type(row['conferenceref'])!=float:
        event_url_raw=html.unescape(row['conferenceref'])
    else:
        event_url_raw=None
    if type(row['host'])!=float:
        host_university_raw=html.unescape(row['host'])
    else:
        host_university_raw=None
    if type(row['authors'])!=float:
        author_ids_l=[]
        if ' and ' in html.unescape(row['authors']):
            print('yes')
            row['authors']=row['authors'].replace(' and ',',')
        firstSplit_l=html.unescape(row['authors']).split(',')

        for c_split in range(0,len(firstSplit_l)):
            print('firstSplit_l',firstSplit_l)
            try:
                mem_id = Member.objects.filter(last_name__contains=html.unescape(firstSplit_l[c_split]).split(' ')[-1].strip('</u>'))[0].id
                # mem_id = Member.objects.filter(last_name__contains=html.unescape(firstSplit_l[c_split]).split(' ')[-1].strip('</u>')).filter(given_name__startwith=html.unescape(firstSplit_l[c_split]).split(' ')[0].replace('<u>','').replace('.',''))[0].id
                print('geschafft')
            except:
                #if mem_id==None:
                print('mem_id is none')
                try:
                    mem_id = Member.objects.filter(last_name_alt__contains=html.unescape(firstSplit_l[c_split]).split(' ')[-1].strip('</u>'))[0].id
                    # mem_id = Member.objects.filter(last_name__contains=html.unescape(firstSplit_l[c_split]).split(' ')[-1].strip('</u>')).filter(given_name__startwith=html.unescape(firstSplit_l[c_split]).split(' ')[0].replace('<u>','').replace('.',''))[0].id
                except:
                    mem_id=None
                    continue
            print(mem_id,type(mem_id))
            author_ids_l.append(mem_id)
            print(mem_id,'SPEAKER')
        speaker_char_raw=html.unescape(row['authors'])
        if len(author_ids_l)==0:
            no_speaker=True
        # Presentation.add(speaker_raw.id)
        #speaker_char_raw=html.unescape(row['speaker'])
    elif type(row['author'])!=float:
        author_ids_l=[]
        if ' and ' in html.unescape(row['authors']):
            print('yes')
            row['author']=row['author'].replace(' and ',',')
        firstSplit_l=html.unescape(row['author']).split(',')

        for c_split in range(0,len(firstSplit_l)):
            print('firstSplit_l',firstSplit_l)
            try:
                mem_id = Member.objects.filter(last_name__contains=html.unescape(firstSplit_l[c_split]).split(' ')[-1].strip('</u>'))[0].id
                # mem_id = Member.objects.filter(last_name__contains=html.unescape(firstSplit_l[c_split]).split(' ')[-1].strip('</u>')).filter(given_name__startwith=html.unescape(firstSplit_l[c_split]).split(' ')[0].replace('<u>','').replace('.',''))[0].id
            except:
                #if mem_id==None:
                print('mem_id is none')
                try:
                    mem_id = Member.objects.filter(last_name_alt__contains=html.unescape(firstSplit_l[c_split]).split(' ')[-1].strip('</u>'))[0].id
                    # mem_id = Member.objects.filter(last_name__contains=html.unescape(firstSplit_l[c_split]).split(' ')[-1].strip('</u>')).filter(given_name__startwith=html.unescape(firstSplit_l[c_split]).split(' ')[0].replace('<u>','').replace('.',''))[0].id
                    print('geschafft')
                except:
                    mem_id=None
                    continue
            print(mem_id,type(mem_id))
            author_ids_l.append(mem_id)
            print(mem_id,'SPEAKER')
        speaker_char_raw=html.unescape(row['author'])
        if len(author_ids_l)==0:
            no_speaker=True
    else:
        speaker_char_raw=None
    if type(row['conference'])!=float:
        event_title_raw=html.unescape(row['conference'])
    elif type(row['invitedfor'])!=float:
        event_title_raw=html.unescape(row['invitedfor'])
    else:
        event_title_raw=None
    if type(row['where'])!=float:
        location_raw=html.unescape(row['where'])
    else:
        location_raw=None
    if type(row['type'])!=float:
        presentation_type_raw=html.unescape(row['type'])
        presentation_type_alt_raw=None
    else:
        presentation_type_raw=None
        presentation_type_alt_raw=None
    if type(row['field'])!=float:
        field_raw=html.unescape(row['field'])
    else:
        field_raw=None
    if type(row['department'])!=float:
        host_department_raw=html.unescape(row['department'])
    else:
        host_department_raw=None
    if type(row['abstract'])!=float:
        abstract_raw=html.unescape(row['abstract'])
    else:
        abstract_raw=None
    if type(row['abstractrefpdf'])!=float:
        abstract_file_raw=html.unescape(row['abstractrefpdf'])
    else:
        abstract_file_raw=None
    if type(row['sliderefpdf'])!=float:
        slides_raw=row['sliderefpdf']
    else:
        slides_raw=None
    try:
        if "workshop" in event_title_raw:
            print(event_title_raw)
            event_type_raw=Event_type.objects.get(id=3)
        elif "conference" in event_title_raw:
            event_type_raw=Event_type.objects.get(id=1)
        else:
            event_type_raw=Event_type.objects.get(id=1)
    except:
        print("no title?",event_title_raw)
        event_type_raw=Event_type.objects.get(id=1)
        pass
    date_start_raw = f"{year_start_raw}-{month_start_raw}-{day_start_raw}"
    date_end_raw = f"{year_end_raw}-{month_end_raw}-{day_end_raw}"
    print('host_university_raw',host_university_raw)
    print('time_raw',time_start_raw,time_end_raw)
    print('date_start_raw',date_start_raw, date_end_raw)
    print('title',title_raw)
    if len(comment_date_raw_l)!=0:
        comment_date_raw=''.join(comment_date_raw_l)
    else:
        comment_date_raw=None
    try:
        if "colloquium" in presentation_type_raw:
            print(presentation_type_raw)
            presentation_type_raw=Presentation_type.objects.get(id=2)
        if "Colloquium" in presentation_type_raw:
            print(presentation_type_raw)
            presentation_type_raw=Presentation_type.objects.get(id=2)
        elif "Kolloquium" in presentation_type_raw:
            presentation_type_raw=Presentation_type.objects.get(id=2)
        elif "kolloquium" in presentation_type_raw:
            presentation_type_raw=Presentation_type.objects.get(id=2)
        elif "seminar" in presentation_type_raw:
            presentation_type_raw=Presentation_type.objects.get(id=1)
        elif "Seminar" in presentation_type_raw:
            presentation_type_raw=Presentation_type.objects.get(id=1)
        elif "poster" in presentation_type_raw:
            presentation_type_raw=Presentation_type.objects.get(id=3)
        elif "Poster" in presentation_type_raw:
            presentation_type_raw=Presentation_type.objects.get(id=3)
        elif "talk" in presentation_type_raw:
            presentation_type_raw=Presentation_type.objects.get(id=4)
        elif "Talk" in presentation_type_raw:
            presentation_type_raw=Presentation_type.objects.get(id=4)
        elif "invited" in presentation_type_raw:
            presentation_type_raw=Presentation_type.objects.get(id=5)
        elif "Invited" in presentation_type_raw:
            presentation_type_raw=Presentation_type.objects.get(id=5)
        else:
            presentation_type_alt_raw=presentation_type_raw
            presentation_type_raw=None
            if presentation_type_alt_raw!=None:
                if "??" in presentation_type_alt_raw:
                    presentation_type_alt_raw=None
    except:
        presentation_type_alt_raw=presentation_type_raw
        presentation_type_raw=None
        if presentation_type_alt_raw!=None:
            if "??" in presentation_type_alt_raw:
                    presentation_type_alt_raw=None
    pass
    new_presentation = Presentation(    start_date=date_start_raw,
                                              end_date=date_end_raw,
                                              comment_date=comment_date_raw,
                          title=title_raw,
                            nonmiei=nonmiei_raw,
                            image=image_raw,
                            author_char=speaker_char_raw,
                            start_time=time_start_raw,
                            end_time=time_end_raw,
                          host_department=host_department_raw,
                            presentation_type=presentation_type_raw,
                            presentation_type_alt=presentation_type_alt_raw,
                            location=location_raw,
                            event_title=event_title_raw,
                            event_url=event_url_raw,
                            event_type=event_type_raw,
                            host_university=host_university_raw,
                            host_person=host_person_raw,
                            host_url=host_url_raw,
                          abstract=abstract_raw,
                            field=field_raw,
                            abstract_file=abstract_file_raw,
                            abstract_ref=abstract_ref_raw,
                            slide_ref=slide_ref_raw,
                            slides=slides_raw)
   
    new_presentation.save()
    if not no_speaker:
        for c_ids in range(0,len(author_ids_l)):
            new_presentation.author.add(author_ids_l[c_ids])
    time.sleep(0.25)

firstSplit_l ['Gianaurelio Cuniberti']
geschafft
2429 <class 'int'>
2429 SPEAKER
host_university_raw None
time_raw None None
date_start_raw 2019-12-20 2019-12-20
title SiNW-based FETs: sensors and neurotransistors
firstSplit_l ['Gianaurelio Cuniberti']
geschafft
2429 <class 'int'>
2429 SPEAKER
host_university_raw None
time_raw None None
date_start_raw 2019-11-28 2019-11-28
title SiNW-based transistors with intrinsic plasticity: from artificial synapses to neurotransistors
firstSplit_l ['Gianaurelio Cuniberti']
geschafft
2429 <class 'int'>
2429 SPEAKER
host_university_raw None
time_raw None None
date_start_raw 2019-07-13 2019-07-13
title The missing sense
firstSplit_l ['Gianaurelio Cuniberti']
geschafft
2429 <class 'int'>
2429 SPEAKER
host_university_raw TU Dresden
time_raw 14:30 14:50
date_start_raw 2018-05-04 2018-05-04
title Cross-scale description of crack propagation in carbon fibre microstructures
firstSplit_l ['Gianaurelio Cuniberti']
geschafft
2429 <class 'int'>
2429 SPEAKER
hos

Old stuff:

In [ ]:
int('    ')